In [1]:
import pandas as pd
import folium, copy, queue
import numpy as np
import networkx as nx
from haversine import haversine
import tkinter as tk
from tkinter import ttk
import tkinterhtml as tkhtml
import webbrowser

In [12]:
# data = pd.read_csv('jeju_market.csv')
# df_rest = data[data['상권업종대분류명'] == '음식']
# df_rest = df_rest[:30]
# df_rest.head()

In [11]:
# df_rest = df_rest[['상호명', 'latitude', 'longitude']]
# list_rest = [1, 1, 1, 1, 1, 1, 0, 1, 0, 1, 0, 0, 0, 0, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 0, 0, 1, 1]
# list_post = [34, 200, 31, 3, 42, 543, 23, 11, 2, 3, 34, 200, 31, 3, 42, 543, 23, 11, 2, 3, 34, 200, 31, 3, 42, 543, 23, 11, 2, 3]

# df_rest['is_rest'] = list_rest
# df_rest['post_num'] = list_post

# df_rest

In [27]:
df_rest = pd.read_csv('output.csv')
df_rest.columns = ['상호명', 'post_num', 'address', 'latitude', 'longitude', 'is_rest']
df_rest.head()

상호명  post_num                    address   latitude   longitude  \
0    더비치크랩       174  제주특별자치도 서귀포시 안덕면 사계남로 168  33.228210  126.307761   
1     지구상회       129  제주특별자치도 제주시 애월읍 애월해안로 715  33.477420  126.363255   
2   제주세원이네        11        제주특별자치도 제주시 삼성로 69   33.508152  126.531497   
3  탄탄흑돈양꼬치         3    제주특별자치도 제주시 한림읍 한림로 687  33.416245  126.265001   
4     자매국수         2       제주특별자치도 제주시 탑동로11길 6  33.517014  126.517833   

   is_rest  
0        1  
1        1  
2        1  
3        1  
4        1

In [24]:
def calDist(graph, curnode): #curnode는 노드 이름
    disDict = {}
    shortest_paths = nx.single_source_dijkstra_path_length(graph, source=curnode, weight='weight') ## cutoff는 curPos로부터최대 거리(이이상은 안찾음)
    for node, distance in shortest_paths.items():
        if node < 10000 and distance>0: ##node들은 4050000000이상임 음식점은 그것보다 작게 설정
            disDict[node] = distance 

    # print(len(disDict))
    return disDict


In [25]:
nodes = pd.read_csv('Jeju_nodes.csv')
links = pd.read_csv('Jeju_links.csv')

nodes = nodes[['Id','NODE_NAME','latitude','longitude']]
links = links[['Source','Target','LENGTH']]
source_in = links['Source'].apply(lambda x : x in list(nodes['Id'])) # check Sources are in jeju_id
target_in = links['Target'].apply(lambda x : x in list(nodes['Id'])) # check Targets are in jeju_id
# source_in and target_in are boolean type pandas.Series which contains True or False
Jeju_links = links[source_in & target_in] # contain if both target and source are contained in jeju_id
G = nx.Graph()

for idx,row in nodes.iterrows():
    G.add_node(row['Id'],Label=row['NODE_NAME'],latitude=row['latitude'], longitude=row['longitude'])

for idx,row in Jeju_links.iterrows():    
    G.add_edge(row['Source'],row['Target'],weight = row['LENGTH'])

print(f"Nodes: {len(G.nodes)}, Edges: {len(G.edges)}")


Nodes: 4218, Edges: 6017


*ADDING LINK(너무 긴 링크의 경우 잘라서 노드를 추가하기)

In [6]:
# Maximum length for a single link (adjust as needed)
"""
max_length = 500  # 예시로 500으로 설정

new_nodes_data = []  # 새로 생성된 노드 데이터를 저장할 리스트
new_links_data = []  # 새로 생성된 링크 데이터를 저장할 리스트

for idx, row in Jeju_links.iterrows():
    source_node = row['Source']
    target_node = row['Target']
    length = row['LENGTH']

    if length > max_length:
        # Calculate the number of intermediate nodes required
        num_intermediate_nodes = int(length / max_length)

        # Calculate the coordinates of the intermediate nodes
        source_lat, source_lon = nodes[nodes['Id'] == source_node][['latitude', 'longitude']].values[0]
        target_lat, target_lon = nodes[nodes['Id'] == target_node][['latitude', 'longitude']].values[0]

        for i in range(1, num_intermediate_nodes + 1):
            fraction = i / (num_intermediate_nodes + 1)
            lat = source_lat + fraction * (target_lat - source_lat)
            lon = source_lon + fraction * (target_lon - source_lon)
            node_id = f"intermediate_{idx}_{i}"  # Unique node id for intermediate node

            new_nodes_data.append([node_id, f"Intermediate {i}", lat, lon])
            new_links_data.append([node_id, target_node, max_length])

            # Update target_node for the next iteration
            target_node = node_id

# Add intermediate nodes and links to the dataframes
new_nodes_df = pd.DataFrame(new_nodes_data, columns=['Id', 'NODE_NAME', 'latitude', 'longitude'])
new_links_df = pd.DataFrame(new_links_data, columns=['Source', 'Target', 'LENGTH'])

# Concatenate the new data with the existing data
nodes = pd.concat([nodes, new_nodes_df], ignore_index=True)
Jeju_links = pd.concat([Jeju_links, new_links_df], ignore_index=True)
"""

'\nmax_length = 500  # 예시로 500으로 설정\n\nnew_nodes_data = []  # 새로 생성된 노드 데이터를 저장할 리스트\nnew_links_data = []  # 새로 생성된 링크 데이터를 저장할 리스트\n\nfor idx, row in Jeju_links.iterrows():\n    source_node = row[\'Source\']\n    target_node = row[\'Target\']\n    length = row[\'LENGTH\']\n\n    if length > max_length:\n        # Calculate the number of intermediate nodes required\n        num_intermediate_nodes = int(length / max_length)\n\n        # Calculate the coordinates of the intermediate nodes\n        source_lat, source_lon = nodes[nodes[\'Id\'] == source_node][[\'latitude\', \'longitude\']].values[0]\n        target_lat, target_lon = nodes[nodes[\'Id\'] == target_node][[\'latitude\', \'longitude\']].values[0]\n\n        for i in range(1, num_intermediate_nodes + 1):\n            fraction = i / (num_intermediate_nodes + 1)\n            lat = source_lat + fraction * (target_lat - source_lat)\n            lon = source_lon + fraction * (target_lon - source_lon)\n            node_id = f"intermed

데이터에 새로 노드들 추가하기

In [28]:
def connectRes(graph, df): # df는 idx, latitude, longitude가 있어야함
    nodes_latitude = nx.get_node_attributes(graph, 'latitude')
    nodes_longitude = nx.get_node_attributes(graph, 'longitude')
    for idx, row in df.iterrows():
        distances ={}
        for keyLong, valLat in nodes_latitude.items():
            nodesPos = (valLat, nodes_longitude[keyLong])
            curPos = (row['latitude'], row['longitude'])
            distances[keyLong] = haversine(nodesPos, curPos, unit='km')
        nearest_node = min(distances, key=distances.get)
        graph.add_node(idx, Label=row['상호명'], latitude=row['latitude'], longitude=row['longitude']) ##노드이름은 4050000000이하로 설정
        graph.add_edge(nearest_node, idx, weight=distances[nearest_node]) 
    return graph

G = connectRes(G, df_rest)
print(f"Data: {len(df_rest)}, Nodes: {len(G.nodes)}, Edges: {len(G.edges)}")

Data: 153, Nodes: 4371, Edges: 6256


In [29]:
G[0]

AtlasView({4060108200: {'weight': 0.5693868291592592}, 0: {'weight': 0.0}})

In [30]:
print(calDist(G, 1))


{88: 0.7366633034901636, 69: 1787.1832833639824, 82: 1787.1832833639824, 116: 2690.8319187793427, 80: 4509.053307303229, 85: 4867.968676470893, 117: 5427.822537616121, 54: 5629.699909418884, 91: 6298.52506418424, 152: 7067.565477968832, 123: 7966.701349088282, 131: 8971.193842657352, 52: 9470.722495496248, 53: 10093.247668769729, 65: 10093.247668769729, 137: 10807.862744829581, 44: 11630.118569152137, 125: 11634.585117187056, 104: 11646.267843137955, 71: 11678.031654579923, 78: 11683.44365955288, 64: 12451.936631559827, 103: 12547.814242979395, 138: 12556.990661262926, 149: 12616.090515903952, 87: 12747.926008921157, 50: 12784.30993726408, 118: 13159.37567160278, 95: 13159.426561563238, 105: 13300.507707373534, 129: 13516.89624273583, 49: 13516.94011057839, 84: 13516.94011057839, 3: 13526.000253214124, 9: 13526.000253214124, 13: 13526.000253214124, 37: 13526.000253214124, 112: 13526.000253214124, 113: 13526.000253214124, 119: 13526.000253214124, 93: 13759.924530954993, 48: 13858.690945

FOLIUM

In [31]:
std_point = tuple(nodes.head(4000)[['latitude','longitude']].iloc[3000]) # example of why we should add nodes

map_osm = folium.Map(location=std_point, zoom_start=12) 

# 도로망 표시
kw = {'opacity': 0.5, 'weight': 2}
for edge in G.edges(data=True):
    source, target, attributes = edge

    # Check if the source and target nodes exist in the graph
    if source in G.nodes and target in G.nodes:
        start = tuple([G.nodes[source]['latitude'], G.nodes[source]['longitude']])
        end = tuple([G.nodes[target]['latitude'], G.nodes[target]['longitude']])

        folium.PolyLine(
            locations=[start, end],
            color='blue',
            line_cap='round',
            **kw,
        ).add_to(map_osm)
    else:
        print(source, target)


# 식당 표시
for ix, row in df_rest.iterrows():
    location = (row['latitude'], row['longitude']) 
    folium.Circle(
        location=location,
        radius=500, 
        color='white',
        weight=1,
        fill_opacity=0.6,
        opacity=1,
        fill_color='red',
        fill=True,  
    ).add_to(map_osm)

# node 표시
for ix, row in nodes.iterrows():
    location = (row['latitude'], row['longitude']) 
    folium.Circle(
        location=location,
        radius=10, 
        color='white',
        weight=1,
        fill_opacity=0.6,
        opacity=1,
        fill_color='black',
        fill=True, 
    ).add_to(map_osm)

map_osm.add_child(folium.LatLngPopup())

### route optimize

In [11]:
# node_graph = nx.Graph()
# node_list_in_graph = []

# for i in range(len(df_rest)):
#     row = df_rest.loc[i]
#     node_graph.add_node(i,Label=row['상호명'],latitude=row['latitude'], longitude=row['longitude'])
#     node_list_in_graph.append(i)

# for source_node in node_list_in_graph:
#     shortest_path_lengths = nx.single_source_dijkstra_path_length(G, source=source_node)

#     for dest_node, distance in shortest_path_lengths.items():
#         if source_node != dest_node and dest_node in node_list_in_graph:  # Avoid self-loops
#             node_graph.add_edge(source_node, dest_node, weight=distance)

# print(node_graph)

### navigate

In [32]:
def navigation(n, graph, curr_node, visited_node, dist, df, min_lst):
    if len(visited_node) > n:
        min_lst.append({'visited_node': visited_node, 'dist': dist})
        return
    
    lst = calDist(graph, curr_node)

    for key, value in lst.items():
        node = df.loc[key]
        lst[key] = value / (np.log(node['post_num']  + 1))

        if node['is_rest'] == df['is_rest'].loc[curr_node]:
            lst[key] = 100000000000
    
    min_item = min(lst, key=lst.get)
    # print(min_item)

    updated_dist = 0

    for key, value in lst.items():
        if value < lst[min_item] * 100 and key not in visited_node:
            tmp = copy.deepcopy(visited_node)
            tmp.append(key)
            result = navigation(n, graph, key, tmp, dist + value, df, min_lst)
            if result:
                return result

        # print([key, value])

In [33]:
def mapping(graph, df, node_list):
    map_osm_2 = folium.Map(location=[33.36364, 126.5639], zoom_start=10.5) 

    # 식당 표시
    for ix, row in df.iterrows():
        location = (row['latitude'], row['longitude']) 
        folium.Circle(
            location=location,
            radius=500, 
            color='white',
            weight=1,
            fill_opacity=0.6,
            opacity=1,
            fill_color='red',
            fill=True,  
        ).add_to(map_osm_2)

    for node_id in node_list:
        node = df.loc[node_id]
        location = (node['latitude'], node['longitude'])

        tooltip_text = f"출발지" if node_list.index(node_id) == 0 else f"{node_list.index(node_id)} 번째 장소<br>{node['상호명']}"
        marker_color = 'red' if node_list.index(node_id) == 0 else 'blue'

        folium.Marker(location, 
            icon=folium.Icon(color=marker_color),
            tooltip=folium.Tooltip(text=tooltip_text)).add_to(map_osm_2)


    # 노드 간의 경로를 Folium 지도에 추가
    for i in range(len(node_list)-1):
        start_node = node_list[i]
        end_node = node_list[i+1]
        path = nx.shortest_path(graph, source=start_node, target=end_node)

        print(path)
        # 경로의 좌표를 리스트로 변환
        path_coordinates = [(graph.nodes[node]['latitude'], graph.nodes[node]['longitude']) for node in path]
            
        # 경로를 선으로 추가
        folium.PolyLine(locations=path_coordinates, color='blue', weight=3).add_to(map_osm_2)

    return map_osm_2, node_list

In [14]:
# modified_graph = copy.deepcopy(graph)
# data = {
#     '상호명': ['src'],
#     'latitude': [src[0]],
#     'longitude': [src[1]]
# }
# df = pd.DataFrame(data)
# df = df.set_index(pd.Index([9999]))
# connectRes(modified_graph, df=df)

In [42]:
def find_path(graph, src, n):
    modified_graph = copy.deepcopy(graph)
    data = {
        '상호명': ['src'],
        'latitude': [src[0]],
        'longitude': [src[1]]
    }
    df = pd.DataFrame(data)
    df = df.set_index(pd.Index([9999]))
    connectRes(modified_graph, df=df)
    
    node_graph = nx.Graph()
    node_list_in_graph = [9999]

    node_graph.add_node(9999, Label='출발지', latitude=src[0], longitude=src[1])

    for i in range(len(df_rest)):
        row = df_rest.loc[i]
        dist_with_src = (((src[0] - row['latitude'])*111)**2 + ((src[1] - row['longitude'])*88)**2)**(1/2) # 위도 1도는 약 111km이고 경도 1도는 약 88km (서울)
        # print(dist_with_src)
        if dist_with_src < 20:
            node_graph.add_node(i, Label=row['상호명'], latitude=row['latitude'], longitude=row['longitude'])
            node_list_in_graph.append(i)

    for source_node in node_list_in_graph:
        shortest_path_lengths = nx.single_source_dijkstra_path_length(modified_graph, source=source_node)

        for dest_node, distance in shortest_path_lengths.items():
            if source_node != dest_node and dest_node in node_list_in_graph:  # Avoid self-loops
                node_graph.add_edge(source_node, dest_node, weight=distance)
    print('done')

    visited_node = [9999]
    dist = 0

    df_added_src = copy.deepcopy(df_rest)
    new_row = pd.DataFrame({'상호명': ['src'], 'latitude': [src[0]], 'longitude': [src[1]]}, index=[9999])
    df_added_src = pd.concat([df_added_src, new_row])

    min_lst = []
    navigation(n, node_graph, 9999, visited_node, dist, df_added_src, min_lst)

    print(f"length of min_lst = {len(min_lst)}")

    min_dist_entry = min(min_lst, key=lambda x: x['dist'])

    print(f"shotest path = {min_dist_entry['visited_node']}")

    return mapping(modified_graph, df_added_src, min_dist_entry['visited_node'])

In [35]:
def show_map():
    src_input = entry_node_list.get()
    src = [float(node) for node in src_input.split(',')]

    # src = [33.39214, 126.4939]
    navigated_map, node_num_list = find_path(G, src, n=3)

    node_list = []

    for node in node_num_list:
        if node == 9999:
            node_list.append("출발지")
        else:
            rest_name = df_rest['상호명'].loc[node]
            is_rest = df_rest['is_rest'].loc[node]
            if is_rest:
                node_list.append(f"{rest_name}, (식당)")
            else:
                node_list.append(f"{rest_name}, (카페)")

    path_string = " -> ".join(node_list)

    # Update the label to display the path
    path_label.config(text=path_string)

    navigated_map.save("map.html")
    webbrowser.open("map.html")

### Application implement

In [36]:
def open_in_browser(map_osm_2):
    map_osm_2.save("map.html")
    webbrowser.open("map.html")

In [46]:
win = tk.Tk()
win.geometry("600x300")
win.title("제주도 인스타 핫플경로")
win.option_add("*Font", "맑은고딕 15")

entry_label = ttk.Label(win, text="출발지의 위, 경도를 입력하세요 (comma-separated):")
entry_label.pack(pady=10)

entry_node_list = ttk.Entry(win)
entry_node_list.pack(pady=10)

show_map_button = ttk.Button(win, text="Show Map", command=show_map)
show_map_button.pack(pady=10)

path_label = ttk.Label(win, text="", wraplength=500, anchor='w', justify='left', padding=(10, 5))
path_label.pack(pady=10)

separator = ttk.Separator(win, orient='horizontal')
separator.pack(pady=(0, 10), anchor='center', fill='x', expand=True)

win.mainloop()

29.481582309171202
22.553767096007444
15.372141188662638
28.564260680419196
16.70139584632618
17.918023612398375
13.320518026839894
34.408936251789896
25.637603445778414
28.564260680419196
9.718078701408778
22.339268006631183
24.628953466700864
28.564260680419196
22.553767096007444
28.675536719133614
13.320518026839894
18.074918488343116
16.738985734975653
19.731679723019287
16.658900628534848
13.2089695840685
28.98536759116556
28.376764069222595
28.376764069222595
30.026444159785093
29.15997746034223
22.114530309486078
29.06363576823701
14.460874919941245
30.19224664016241
29.744964976828328
25.611663940757097
14.445072549785205
15.619891790191904
19.561922687793313
14.411830316115317
28.564260680419196
15.658089218993478
12.990395530625133
28.376764069222595
14.68317404562622
13.482926606189404
30.02489810910656
16.296340971700264
11.004482309478966
18.00247850410391
22.651853773952563
14.877225505846189
13.857408518487773
15.1713202428613
19.805462415561962
17.193378353021934
27.614